# Inspector

#### What is inspector ?  
   Vai_q_pytorch provides a function called inspector to help users diagnose neural network (NN) models under different device architectures. The inspector can predict target device assignments based on hardware constraints.The generated inspection report can be used to guide  users to modify or optimize the NN model, greatly reducing the difficulty and time of deployment. It is recommended to inspect float models before quantization.

In [1]:
import torch

import sys
import os
os.environ["CUDA_VISIBLE_DEVICES"]="0"

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

if torch.cuda.is_available():
    print("Available GPUs:", torch.cuda.device_count())
    for i in range(torch.cuda.device_count()):
        print(f"GPU {i}: {torch.cuda.get_device_name(i)}")
else:
    print("No GPUs available, CPU {} ".format(device))

yolov5_dir = '/workspace/YOLO/YOLOv5'
sys.path.append(yolov5_dir)
# os.chdir(yolov5_dir)
# import utils
# display = utils.notebook_init()  # checks

from models.common import DetectMultiBackend

Available GPUs: 1
GPU 0: NVIDIA GeForce RTX 3080


In [2]:
# Import inspector API
# 
# Note:
# You can ignore warning message related with XIR. 
# The inspector relies on 'vai_utf' package. In conda env vitis-ai-pytorch in Vitis-AI docker, vai_utf is ready. But if vai_q_pytorch is installed by source code, it needs to install vai_utf in advance.
from pytorch_nndct import Inspector


[VAIQ_NOTE]: Loading NNDCT kernels...


In [3]:
model_dir = '/workspace/jupyter_notebooks/VAI_3.5/dms_yolov5n/dms_yolov5nLeaky.pt'

In [4]:
# Define a toy neural network
# model = torch.hub.load('.', 'custom', path=model_dir, source='local', autoshape=False)  # Load custom model from local path, ensure reloading is controlled
model = DetectMultiBackend(model_dir, device=device) # Load custom model from local path, ensure reloading is controlled

Fusing layers... 
YOLOv5n-LeakyReLU summary: 157 layers, 1771342 parameters, 0 gradients, 4.2 GFLOPs


In [5]:
from torchinfo import summary
summary(model, (1, 3, 480, 480))  # Display model summary for specified input size

Layer (type:depth-idx)                                  Output Shape              Param #
DetectMultiBackend                                      [1, 42, 60, 60]           --
├─DetectionModel: 1-1                                   [1, 42, 60, 60]           --
│    └─Sequential: 2-1                                  --                        --
│    │    └─Conv: 3-1                                   [1, 16, 240, 240]         (1,744)
│    │    └─C3: 3-109                                   --                        (recursive)
│    │    └─Conv: 3-3                                   [1, 32, 120, 120]         (4,640)
│    │    └─C3: 3-109                                   --                        (recursive)
│    │    └─C3: 3-5                                     [1, 32, 120, 120]         (4,704)
│    │    └─C3: 3-109                                   --                        (recursive)
│    │    └─C3: 3-13                                    --                        (recursive)
│    │   

In [6]:
# Specify a target name or fingerprint you want to deploy on
target = "DPUCZDX8G_ISA1_B4096"
# Initialize inspector with target
inspector = Inspector(target)


[VAIQ_NOTE]: Inspector is on.


In [7]:
# Start to inspect the float model
# Note: visualization of inspection results relies on the dot engine.If you don't install dot successfully, set 'image_format = None' when inspecting.
dummy_input = torch.randn([1, 3, 480, 480], device=device)

inspector.inspect(model, (dummy_input,), device=device, output_dir="inspect", image_format="png") 


[VAIQ_NOTE]: =>Start to inspect model...

[VAIQ_NOTE]: =>Quant Module is in 'cuda'.

[VAIQ_NOTE]: =>Parsing DetectMultiBackend...

[VAIQ_NOTE]: Start to trace and freeze model...

[VAIQ_NOTE]: The input model nndct_st_DetectMultiBackend_ed is torch.nn.Module.

[VAIQ_NOTE]: Finish tracing.

[VAIQ_NOTE]: Processing ops...


██████████████████████████████████████████████████| 144/144 [00:00<00:00, 1125.48it/s, OpInfo: name = return_0, type = Return]                                                        


[VAIQ_NOTE]: =>Doing weights equalization...



[VAIQ_WARN][QUANTIZER_TORCH_LEAKYRELU]: Preserve negative_slope(0.1015625) of LeakyReLU without quantization.

[VAIQ_NOTE]: =>Quantizable module is generated.(inspect/DetectMultiBackend.py)

[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Conv[cv1]/Conv2d[conv]/ret.149, op type:nndct_conv2d, output shape: [1, 15, 15, 128]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Conv[cv1]/LeakyReLU[act]/11184, op type:nndct_leaky_relu, output shape: [1, 15, 15, 128]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv2]/Conv2d[conv]/ret.65, op type:nndct_conv2d, output shape: [1, 30, 30, 64]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv2]/LeakyReLU[act]/10443, op type:nndct_leaky_relu, output shape: [1, 30, 30, 64]



[VAIQ_NOTE]

I20241113 11:21:51.617486  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:51.617525  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:51.617533  4008 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241113 11:21:51.617594  4008 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_YzK51EBQmlaq0sCu, with op num: 9
I20241113 11:21:51.617597  4008 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241113 11:21:51.620905  4008 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241113 11:21:51.620921  4008 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241113 11:21:51.623958  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:51.623986  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:51.623992  4008 


[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv1]/Conv2d[conv]/ret.45, op type:nndct_conv2d, output shape: [1, 30, 30, 64]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv1]/LeakyReLU[act]/10280, op type:nndct_leaky_relu, output shape: [1, 30, 30, 64]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[13]/Conv[cv3]/Conv2d[conv]/ret.109, op type:nndct_conv2d, output shape: [1, 30, 30, 128]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[13]/Conv[cv3]/LeakyReLU[act]/10850, op type:nndct_leaky_relu, output shape: [1, 30, 30, 128]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Conv[model]/Conv[18]/Conv2d[conv]/ret.129, op type:nndct_conv2d, output shape: [1, 

I20241113 11:21:51.823894  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:51.823920  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:51.823926  4008 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241113 11:21:51.823985  4008 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_W1bxPsUXnmJEBA3c, with op num: 9
I20241113 11:21:51.823992  4008 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241113 11:21:51.826226  4008 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241113 11:21:51.826242  4008 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241113 11:21:51.829320  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:51.829349  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:51.829355  4008 


[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Concat[model]/Concat[19]/ret.131, op type:nndct_concat, output shape: [1, 30, 30, 128]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/SPPF[model]/SPPF[9]/ret.89, op type:nndct_concat, output shape: [1, 15, 15, 512]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Concat[model]/Concat[16]/ret.115, op type:nndct_concat, output shape: [1, 60, 60, 128]



[VAIQ_NOTE]: Find subgraph for convlike_fix_20:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Detect[model]/Detect[24]/Conv2d[m]/ModuleList[2]/ret, op type:nndct_conv2d, output shape: [1, 15, 15, 42]



[VAIQ_NOTE]: Find subgraph for convlike_fix_20:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Detect[model]/Detect[24]/Conv2d[m]/Mo

I20241113 11:21:52.030200  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:52.030225  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:52.030230  4008 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241113 11:21:52.030270  4008 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_concat_vy08WqFbuGC6OzdJ, with op num: 6
I20241113 11:21:52.030272  4008 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241113 11:21:52.031765  4008 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 4, DPU subgraph number 1
I20241113 11:21:52.031781  4008 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241113 11:21:52.034266  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:52.034329  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:52.034334  4008 compile_pass_mana


[VAIQ_NOTE]: Dot image is generated.(inspect/inspect_DPUCZDX8G_ISA1_B4096.png)

[VAIQ_NOTE]: =>Finish inspecting.


##### Inspection result anaysis:
1. Layers assigned to the CPU are shown in <font color=red>red circle</font> in the dot image. The reasons for being allocated to the CPU are shown in the column of hardware constraints.
2. The target device of an input node is determined by its consumer.
3. Due to data layout difference between Pytorch('NCHW') and XIR('NHWC'), if quantizer inserts some permutes(which the node message in inspect file will inform us about), these permutes may prevent the entire model from being deployed to the target device. Sometimes, we can cancel out this automatically inserted permute by inserting a permute in the original float model, sometimes, we can't.
4. If you want more details about the inspection, see the inspection report under the output directory you specified.
5. The dot image can help you to analyze inspection result in a more intuitive way. "svg" and "png" format are both supported.


In [8]:
# Show the dot image
from IPython.display import Image
Image('inspect/inspect_DPUCZDX8G_ISA1_B4096.png')

##### How to deploy this entire model on DPU:
1. Find the location of CPU operations in original model. All the details of operations are shown in inspect_{target}.txt, including source range, points to a source which is a stack track and helps to find the exact location of this operation in source code. Take resize op as a example, from source range, we can find the location of resize op in #3 input block line 11.  
node name: ToyModel::ToyModel/Upsample[upsample]/input.3  
...  
op type: resize  
...  
source range:  
...  
<font color=red>ipython-input-3-7ec1fc6b678f(11): forward</font>  
...

2. Modify the original model according to the hardware constrains message and try to cancel out the permute inserted by quantizer with by inserting a permute in the original float model(more details see hints in inspect_{target}.txt)

# Quantizer

#### What is quantizer ?  
   The inference process is computationally intensive and requires a high memory bandwidth to satisfy the low-latency and high-throughput requirements of Edge applications.
Quantization and channel pruning techniques address these challenges while simultaneously achieving optimal performance and high energy efficiency with minimal degradation in accuracy. Through quantization, integer computing units become viable, and weights and activations can be represented with reduced precision.

In [9]:
from pytorch_nndct.apis import torch_quantizer

In [10]:
quant_mode = 'calib'
quantizer = torch_quantizer(quant_mode, model, dummy_input, device=device, bitwidth=8, target=target)

quant_model = quantizer.quant_model


[VAIQ_NOTE]: OS and CPU information:
               system --- Linux
                 node --- 6992c15b56b5
              release --- 5.15.153.1-microsoft-standard-WSL2
              version --- #1 SMP Fri Mar 29 23:14:13 UTC 2024
              machine --- x86_64
            processor --- x86_64

[VAIQ_NOTE]: Tools version information:
                  GCC --- GCC 7.5.0
               python --- 3.8.6
              pytorch --- 1.13.1+cu117
        vai_q_pytorch --- 3.5.0+60df3f1+torch1.13.1+cu117

[VAIQ_NOTE]: Quant config file is empty, use default quant configuration

[VAIQ_NOTE]: Quantization calibration process start up...

[VAIQ_NOTE]: =>Quant Module is in 'cuda'.

[VAIQ_NOTE]: =>Parsing DetectMultiBackend...

[VAIQ_NOTE]: Start to trace and freeze model...

[VAIQ_NOTE]: The input model nndct_st_DetectMultiBackend_ed is torch.nn.Module.

[VAIQ_NOTE]: Finish tracing.

[VAIQ_NOTE]: Processing ops...


██████████████████████████████████████████████████| 144/144 [00:00<00:00, 1144.83it/s, OpInfo: name = return_0, type = Return]                                                        


[VAIQ_NOTE]: =>Doing weights equalization...

[VAIQ_NOTE]: =>Quantizable module is generated.(quantize_result/DetectMultiBackend.py)



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Conv[cv1]/Conv2d[conv]/ret.149, op type:nndct_conv2d, output shape: [1, 15, 15, 128]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Conv[cv1]/LeakyReLU[act]/11184, op type:nndct_leaky_relu, output shape: [1, 15, 15, 128]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv2]/Conv2d[conv]/ret.65, op type:nndct_conv2d, output shape: [1, 30, 30, 64]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv2]/LeakyReLU[act]/10443, op type:nndct_leaky_relu, output shape: [1, 30, 30, 64]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[2]/Conv[cv2]/Conv2d[conv]/ret.15, op type:nndct_conv2d, output shape: 

I20241113 11:21:59.555262  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:59.555302  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:59.555311  4008 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241113 11:21:59.555414  4008 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_HDR1pAzo2gxjYfUT, with op num: 9
I20241113 11:21:59.555423  4008 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241113 11:21:59.559660  4008 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241113 11:21:59.559681  4008 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241113 11:21:59.563316  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:59.563344  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:59.563350  4008 


[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[4]/Conv[cv2]/Conv2d[conv]/ret.37, op type:nndct_conv2d, output shape: [1, 60, 60, 32]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[4]/Conv[cv2]/LeakyReLU[act]/10210, op type:nndct_leaky_relu, output shape: [1, 60, 60, 32]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[17]/Sequential[m]/Bottleneck[0]/Conv[cv1]/Conv2d[conv]/ret.119, op type:nndct_conv2d, output shape: [1, 60, 60, 32]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[17]/Sequential[m]/Bottleneck[0]/Conv[cv1]/LeakyReLU[act]/10926, op type:nndct_leaky_relu, output shape: [1, 60, 60, 32]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv1]/Con

I20241113 11:21:59.760322  4008 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_uvAG3L4wDnNxiy9R, with op num: 9
I20241113 11:21:59.760325  4008 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241113 11:21:59.766505  4008 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241113 11:21:59.766525  4008 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241113 11:21:59.770246  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:59.770269  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:59.770274  4008 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241113 11:21:59.770316  4008 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_i34EguLqJDmH0yeA, with op num: 9
I20241113 11:21:59.770319  4008 compile_pass_manager.cpp:478] [UNILOG


[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[2]/ret.17, op type:nndct_concat, output shape: [1, 120, 120, 32]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[20]/ret.141, op type:nndct_concat, output shape: [1, 30, 30, 128]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[8]/ret.83, op type:nndct_concat, output shape: [1, 15, 15, 256]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Concat[model]/Concat[12]/ret.97, op type:nndct_concat, output shape: [1, 30, 30, 256]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/ret.157, op type:nndct_concat, output shape: [1, 15, 15, 256]





I20241113 11:21:59.966893  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:59.966917  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:59.966921  4008 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241113 11:21:59.966966  4008 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_concat_LB07HdZ2cYbPgom3, with op num: 6
I20241113 11:21:59.966971  4008 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241113 11:21:59.968664  4008 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 4, DPU subgraph number 1
I20241113 11:21:59.968680  4008 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241113 11:21:59.971519  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:21:59.971544  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:21:59.971549  4008 compile_pass_mana

In [11]:
# Forward pass
quantizer.quant_model(dummy_input)

# export the quantization results
quantizer.export_quant_config()


[VAIQ_NOTE]: =>Get module with quantization.

[VAIQ_NOTE]: =>Exporting quant config.(quantize_result/quant_info.json)


In [12]:
quant_mode = 'test'
quantizer = torch_quantizer(quant_mode, model, dummy_input, device=device, bitwidth=8, target=target)

quant_model = quantizer.quant_model


[VAIQ_NOTE]: OS and CPU information:
               system --- Linux
                 node --- 6992c15b56b5
              release --- 5.15.153.1-microsoft-standard-WSL2
              version --- #1 SMP Fri Mar 29 23:14:13 UTC 2024
              machine --- x86_64
            processor --- x86_64

[VAIQ_NOTE]: Tools version information:
                  GCC --- GCC 7.5.0
               python --- 3.8.6
              pytorch --- 1.13.1+cu117
        vai_q_pytorch --- 3.5.0+60df3f1+torch1.13.1+cu117

[VAIQ_NOTE]: Quant config file is empty, use default quant configuration

[VAIQ_NOTE]: Quantization test process start up...

[VAIQ_NOTE]: =>Quant Module is in 'cuda'.

[VAIQ_NOTE]: =>Parsing DetectMultiBackend...

[VAIQ_NOTE]: Start to trace and freeze model...

[VAIQ_NOTE]: The input model nndct_st_DetectMultiBackend_ed is torch.nn.Module.

[VAIQ_NOTE]: Finish tracing.

[VAIQ_NOTE]: Processing ops...


██████████████████████████████████████████████████| 144/144 [00:00<00:00, 1147.41it/s, OpInfo: name = return_0, type = Return]                                                        


[VAIQ_NOTE]: =>Doing weights equalization...



[VAIQ_NOTE]: =>Quantizable module is generated.(quantize_result/DetectMultiBackend.py)

[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Conv[cv1]/Conv2d[conv]/ret.149, op type:nndct_conv2d, output shape: [1, 15, 15, 128]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Conv[cv1]/LeakyReLU[act]/11184, op type:nndct_leaky_relu, output shape: [1, 15, 15, 128]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv2]/Conv2d[conv]/ret.65, op type:nndct_conv2d, output shape: [1, 30, 30, 64]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv2]/LeakyReLU[act]/10443, op type:nndct_leaky_relu, output shape: [1, 30, 30, 64]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[mo

I20241113 11:22:01.901779  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:22:01.901809  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:22:01.901815  4008 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241113 11:22:01.901873  4008 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_OzSk2daEjvb18fCX, with op num: 9
I20241113 11:22:01.901876  4008 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241113 11:22:01.904987  4008 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241113 11:22:01.905002  4008 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241113 11:22:01.907886  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:22:01.907914  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:22:01.907920  4008 


[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv1]/Conv2d[conv]/ret.45, op type:nndct_conv2d, output shape: [1, 30, 30, 64]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Conv[cv1]/LeakyReLU[act]/10280, op type:nndct_leaky_relu, output shape: [1, 30, 30, 64]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[13]/Conv[cv3]/Conv2d[conv]/ret.109, op type:nndct_conv2d, output shape: [1, 30, 30, 128]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[13]/Conv[cv3]/LeakyReLU[act]/10850, op type:nndct_leaky_relu, output shape: [1, 30, 30, 128]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Conv[model]/Conv[18]/Conv2d[conv]/ret.129, op type:nndct_conv2d, output shape: [1, 

I20241113 11:22:02.105518  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:22:02.105541  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:22:02.105546  4008 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241113 11:22:02.105577  4008 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_tmvdI98r40X3l7Sy, with op num: 9
I20241113 11:22:02.105580  4008 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241113 11:22:02.107828  4008 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241113 11:22:02.107843  4008 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241113 11:22:02.111097  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:22:02.111126  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:22:02.111132  4008 


[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/ret.157, op type:nndct_concat, output shape: [1, 15, 15, 256]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Concat[model]/Concat[19]/ret.131, op type:nndct_concat, output shape: [1, 30, 30, 128]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/SPPF[model]/SPPF[9]/ret.89, op type:nndct_concat, output shape: [1, 15, 15, 512]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Concat[model]/Concat[16]/ret.115, op type:nndct_concat, output shape: [1, 60, 60, 128]



[VAIQ_NOTE]: Find subgraph for convlike_fix_20:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Detect[model]/Detect[24]/Conv2d[m]/ModuleList[2]/ret, op type:nndc

I20241113 11:22:02.307618  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:22:02.307624  4008 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241113 11:22:02.307658  4008 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_concat_AUd8tjIW13DNkCgK, with op num: 6
I20241113 11:22:02.307662  4008 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241113 11:22:02.309090  4008 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 4, DPU subgraph number 1
I20241113 11:22:02.309106  4008 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241113 11:22:02.311746  4008 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241113 11:22:02.311769  4008 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241113 11:22:02.311774  4008 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241113 11:22:02.311805


[VAIQ_NOTE]: =>Get module with quantization.


In [13]:
# Forward pass
quantizer.quant_model(dummy_input)  # forward pass

quantizer.export_xmodel(deploy_check=False)


[VAIQ_NOTE]: =>Get module with quantization.

[VAIQ_NOTE]: =>Converting to xmodel ...

[VAIQ_NOTE]: =>Successfully convert 'DetectMultiBackend' to xmodel.(quantize_result/DetectMultiBackend_int.xmodel)


### Quantize done
next process is complie .xmodel
```
vai_c_xir -x /PATH/TO/quantized.xmodel -a /PATH/TO/arch.json -o /OUTPUTPATH -n netname
```

In [14]:
!vai_c_xir -x ./quantize_result/DetectMultiBackend_int.xmodel -a /opt/vitis_ai/compiler/arch/DPUCZDX8G/KV260/arch.json -o ./compile/ -n dms_yolov5Leaky

**************************************************
* VITIS_AI Compilation - Xilinx Inc.
**************************************************
[UNILOG][INFO] Compile mode: dpu
[UNILOG][INFO] Debug mode: null
[UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
[UNILOG][INFO] Graph name: DetectMultiBackend, with op num: 448
[UNILOG][INFO] Begin to compile...
[UNILOG][INFO] Total device subgraph number 5, DPU subgraph number 1
[UNILOG][INFO] Compile done.
[UNILOG][INFO] The meta json is saved to "/workspace/jupyter_notebooks/VAI_3.5/dms_yolov5n/./compile/meta.json"
[UNILOG][INFO] The compiled xmodel is saved to "/workspace/jupyter_notebooks/VAI_3.5/dms_yolov5n/./compile//dms_yolov5Leaky.xmodel"
[UNILOG][INFO] The compiled xmodel's md5sum is 7a3d9511abf9d97f9cf8f48ccf2d874f, and has been saved to "/workspace/jupyter_notebooks/VAI_3.5/dms_yolov5n/./compile/md5sum.txt"
